<img  src="http://cdn.slashgear.com/wp-content/uploads/2015/11/google_tensorflow.jpg">

#### Machine learning library

<img style="float: right" src="http://www.tensorflow.org/images/tensors_flowing.gif" width=150 height=100>

#### TensorFlow was originally developed by researchers and engineers working on the Google Brain Team within Google's Machine Intelligence research organization.

#### TensorFlow runs on CPUs or GPUs, and on desktop, server, or mobile computing platforms.

#### Python interface and C++ interface

In [1]:
#import input_data
#mnist = input_data.read_data_sets("MNIST_data/", one_hot=True)
from tensorflow.examples.tutorials.mnist import input_data
mnist = input_data.read_data_sets("MNIST_data/", one_hot=True)

Extracting MNIST_data/train-images-idx3-ubyte.gz
Extracting MNIST_data/train-labels-idx1-ubyte.gz
Extracting MNIST_data/t10k-images-idx3-ubyte.gz
Extracting MNIST_data/t10k-labels-idx1-ubyte.gz


In [2]:
import tensorflow as tf
import time

In [3]:
x = tf.placeholder("float", [None, 784])
W = tf.Variable(tf.zeros([784,10]))
b = tf.Variable(tf.zeros([10]))
y = tf.nn.softmax(tf.matmul(x,W) + b)

In [4]:
y_ = tf.placeholder("float", [None,10])
cross_entropy = -tf.reduce_sum(y_*tf.log(y))

In [5]:
train_step = tf.train.GradientDescentOptimizer(0.01).minimize(cross_entropy)

In [6]:
init = tf.initialize_all_variables()
sess = tf.Session()
sess.run(init)
for i in range(10000):
  batch_xs, batch_ys = mnist.train.next_batch(100)
  sess.run(train_step, feed_dict={x: batch_xs, y_: batch_ys})

Instructions for updating:
Use `tf.global_variables_initializer` instead.


Instructions for updating:
Use `tf.global_variables_initializer` instead.


In [7]:
correct_prediction = tf.equal(tf.argmax(y,1), tf.argmax(y_,1))
accuracy = tf.reduce_mean(tf.cast(correct_prediction, "float"))
print(sess.run(accuracy, feed_dict={x: mnist.test.images, y_: mnist.test.labels}))

0.9208


In [8]:
sess = tf.InteractiveSession()

In [9]:
def weight_variable(shape):
  initial = tf.truncated_normal(shape, stddev=0.1)
  return tf.Variable(initial)

def bias_variable(shape):
  initial = tf.constant(0.1, shape=shape)
  return tf.Variable(initial)

def conv2d(x, W):
  return tf.nn.conv2d(x, W, strides=[1, 1, 1, 1], padding='SAME')

def max_pool_2x2(x):
  return tf.nn.max_pool(x, ksize=[1, 2, 2, 1],
                        strides=[1, 2, 2, 1], padding='SAME')

<img src=http://deeplearning.net/tutorial/_images/mylenet.png>

### First convolutional layer

* compute 32 features for each 5x5 patch
* The weight tensor will have a shape of [5, 5, 1, 32]

In [10]:
W_conv1 = weight_variable([5, 5, 1, 32])
b_conv1 = bias_variable([32])
x_image = tf.reshape(x, [-1,28,28,1])
h_conv1 = tf.nn.relu(conv2d(x_image, W_conv1) + b_conv1)
h_pool1 = max_pool_2x2(h_conv1)

In [11]:
W_conv2 = weight_variable([5, 5, 32, 64])
b_conv2 = bias_variable([64])
h_conv2 = tf.nn.relu(conv2d(h_pool1, W_conv2) + b_conv2)
h_pool2 = max_pool_2x2(h_conv2)

In [12]:
W_fc1 = weight_variable([7 * 7 * 64, 1024])
b_fc1 = bias_variable([1024])
h_pool2_flat = tf.reshape(h_pool2, [-1, 7*7*64])
h_fc1 = tf.nn.relu(tf.matmul(h_pool2_flat, W_fc1) + b_fc1)

In [13]:
keep_prob = tf.placeholder("float")
h_fc1_drop = tf.nn.dropout(h_fc1, keep_prob)

In [14]:
W_fc2 = weight_variable([1024, 10])
b_fc2 = bias_variable([10])
y_conv=tf.nn.softmax(tf.matmul(h_fc1_drop, W_fc2) + b_fc2)

In [15]:
#with tf.device("/gpu:0"):
with tf.device("/cpu:0"):
    cross_entropy = -tf.reduce_sum(y_*tf.log(y_conv))
    train_step = tf.train.AdamOptimizer(1e-4).minimize(cross_entropy)
    correct_prediction = tf.equal(tf.argmax(y_conv,1), tf.argmax(y_,1))
    accuracy = tf.reduce_mean(tf.cast(correct_prediction, "float"))
    sess.run(tf.initialize_all_variables())
    t0=time.time()
    for i in range(20000):
        batch = mnist.train.next_batch(50)
        if i%100 == 0:
            t1=time.time()
            train_accuracy = accuracy.eval(feed_dict={x:batch[0], y_: batch[1], keep_prob: 1.0})
            print("step %d, training accuracy %g in %f sec"%(i, train_accuracy,t1-t0))
            t0=t1
            print("step %d, test accuracy %g"%(i,accuracy.eval(feed_dict={x: mnist.test.images, y_: mnist.test.labels, keep_prob: 1.0})))
        train_step.run(feed_dict={x: batch[0], y_: batch[1], keep_prob: 0.5})
    print("test accuracy %g" % (accuracy.eval(feed_dict={x: mnist.test.images, y_: mnist.test.labels, keep_prob: 1.0})))

Instructions for updating:
Use `tf.global_variables_initializer` instead.


Instructions for updating:
Use `tf.global_variables_initializer` instead.


step 0, training accuracy 0.1 in 0.000478 sec
step 0, test accuracy 0.0947
step 100, training accuracy 0.76 in 40.720867 sec
step 100, test accuracy 0.8598
step 200, training accuracy 0.92 in 36.370875 sec
step 200, test accuracy 0.9108
step 300, training accuracy 0.92 in 38.124666 sec
step 300, test accuracy 0.9295
step 400, training accuracy 0.92 in 37.825192 sec
step 400, test accuracy 0.9364
step 500, training accuracy 0.88 in 36.835875 sec
step 500, test accuracy 0.9449
step 600, training accuracy 0.98 in 36.969428 sec
step 600, test accuracy 0.9532
step 700, training accuracy 0.98 in 35.559626 sec
step 700, test accuracy 0.9558
step 800, training accuracy 0.92 in 43.857148 sec
step 800, test accuracy 0.9608
step 900, training accuracy 0.96 in 37.068362 sec
step 900, test accuracy 0.9627
step 1000, training accuracy 0.98 in 37.166295 sec
step 1000, test accuracy 0.9656
step 1100, training accuracy 0.94 in 35.543291 sec
step 1100, test accuracy 0.9672
step 1200, training accuracy 0

KeyboardInterrupt: 

In [16]:
from keras.datasets import cifar10,mnist
from keras.preprocessing.image import ImageDataGenerator
from keras.models import Sequential, Model
from keras.layers import Dense, Input, Dropout, Activation, Flatten
from keras.layers import Convolution2D, MaxPooling2D, normalization
from keras.utils import np_utils
import keras.backend as K

Using TensorFlow backend.


In [17]:
batch_size = 32
nb_classes = 10
nb_epoch = 10
data_augmentation = True

# input image dimensions
img_rows, img_cols = 32, 32

# The CIFAR10 images are RGB
img_channels = 3

# The data, shuffled and split between train and test sets:
(X_train, y_train), (X_test, y_test) = cifar10.load_data()
print('X_train shape:', X_train.shape)
print(X_train.shape[0], 'train samples')
print(X_test.shape[0], 'test samples')

# Convert class vectors to binary class matrices.
Y_train = np_utils.to_categorical(y_train, nb_classes)
Y_test = np_utils.to_categorical(y_test, nb_classes)

('X_train shape:', (50000, 32, 32, 3))
(50000, 'train samples')
(10000, 'test samples')


In [18]:
model = Sequential()
model.add(Convolution2D(32, 3, 3, border_mode='same', input_shape=X_train.shape[1:]))
model.add(Activation('relu'))
model.add(Convolution2D(32, 3, 3))
model.add(Activation('relu'))
model.add(MaxPooling2D(pool_size=(2, 2)))
model.add(Dropout(0.25))

model.add(Convolution2D(64, 3, 3, border_mode='same'))
model.add(Activation('relu'))
model.add(Convolution2D(64, 3, 3))
model.add(Activation('relu'))
model.add(MaxPooling2D(pool_size=(2, 2)))
model.add(Dropout(0.25))

/Users/balint/.graphlab/anaconda/lib/python2.7/site-packages/IPython/kernel/__main__.py:2: UserWarning: Update your `Conv2D` call to the Keras 2 API: `Conv2D(32, (3, 3), padding="same", input_shape=(32, 32, 3...)`
  from IPython.kernel.zmq import kernelapp as app
/Users/balint/.graphlab/anaconda/lib/python2.7/site-packages/IPython/kernel/__main__.py:4: UserWarning: Update your `Conv2D` call to the Keras 2 API: `Conv2D(32, (3, 3))`
/Users/balint/.graphlab/anaconda/lib/python2.7/site-packages/IPython/kernel/__main__.py:9: UserWarning: Update your `Conv2D` call to the Keras 2 API: `Conv2D(64, (3, 3), padding="same")`
/Users/balint/.graphlab/anaconda/lib/python2.7/site-packages/IPython/kernel/__main__.py:11: UserWarning: Update your `Conv2D` call to the Keras 2 API: `Conv2D(64, (3, 3))`


In [19]:
# FC layer with ReLU
model.add(Flatten())
model.add(Dense(512))
model.add(Activation('relu'))
model.add(Dropout(0.5))

# Output layer 
model.add(Dense(nb_classes))
model.add(Activation('softmax'))

# Train with ADAM
model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])
model.summary()

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
conv2d_1 (Conv2D)            (None, 32, 32, 32)        896       
_________________________________________________________________
activation_1 (Activation)    (None, 32, 32, 32)        0         
_________________________________________________________________
conv2d_2 (Conv2D)            (None, 30, 30, 32)        9248      
_________________________________________________________________
activation_2 (Activation)    (None, 30, 30, 32)        0         
_________________________________________________________________
max_pooling2d_1 (MaxPooling2 (None, 15, 15, 32)        0         
_________________________________________________________________
dropout_1 (Dropout)          (None, 15, 15, 32)        0         
_________________________________________________________________
conv2d_3 (Conv2D)            (None, 15, 15, 64)        18496     
__________

In [20]:
X_train = X_train.astype('float32')
X_test = X_test.astype('float32')
X_train /= 255
X_test /= 255

In [21]:
data_augmentation = False

In [ ]:
if not data_augmentation: 
    print('Not using data augmentation.')    
    model.fit(X_train, Y_train,  batch_size=batch_size, nb_epoch=nb_epoch,
              validation_data=(X_test, Y_test),  shuffle=True)
else:
    print('Using real-time data augmentation.')    
    datagen = ImageDataGenerator( 
        featurewise_center=False,  # set input mean to 0 over the dataset 
        samplewise_center=False,  # set each sample mean to 0 
        featurewise_std_normalization=False,  # divide inputs by std of the dataset 
        samplewise_std_normalization=False,  # divide each input by its std 
        zca_whitening=False,  # apply ZCA whitening        
        rotation_range=0,  # randomly rotate images in the range (0..180 deg)        
        width_shift_range=0.1,  # randomly shift images horizontally (fraction of total width)        
        height_shift_range=0.1,  # randomly shift images vertically (fraction of total height)        
        horizontal_flip=True,  # randomly flip images 
        vertical_flip=False  # randomly flip images    
        )
    datagen.fit(X_train)    # Fit the model on the batches generated by datagen.flow().
    model.fit_generator(datagen.flow(X_train, Y_train, 
                                     batch_size=batch_size), samples_per_epoch=X_train.shape[0],
                                     nb_epoch=nb_epoch, validation_data=(X_test, Y_test))


Not using data augmentation.
Train on 50000 samples, validate on 10000 samples
Epoch 1/10
 1120/50000 [..............................] - ETA: 408s - loss: 2.3128 - acc: 0.0902